### Script for creating subset of articles containing atleast one graph database company and storing it in a collection on local system

In [1]:
from pymongo import MongoClient

In [2]:
from bson import ObjectId

In [3]:
local = MongoClient()

In [4]:
gem = MongoClient('act4dgem.cse.iitd.ac.in')

In [5]:
articlesColl = gem.get_database('media-db').get_collection('articles')

In [24]:
resolved_entities = gem.get_database('eventwise_media-db').get_collection('all_media_entities_resolved_final3')

In [7]:
import pandas as pd

In [8]:
organizationArticles = local.get_database('media-db').get_collection('articlesWithGraphOrg2')

In [9]:
from py2neo import Graph

In [10]:
graph = Graph(host='10.237.27.115')

In [11]:
getName = 'match (x) where x.uuid = {} return x.name as name'

In [12]:
isCompany = 'match (x) where x.uuid = {} return "company" in labels(x) as res'

In [13]:
getCompany = 'match (x:company) return x.cin as cin, x.name as name, x.uuid as uuid'

In [14]:
companyDf = pd.DataFrame(graph.data(getCompany))

In [15]:
companyDf.shape

(93492, 3)

In [16]:
companyDf.head()

cin                              name    uuid
0  L00000CH1983PLC031318            SAB INDUSTRIES LIMITED  154241
1  L00000CH1990PLC010573  LAKSHMI ENERGY AND FOODS LIMITED  154242
2  L00000HP1994PLC014770        HITKARI INDUSTRIES LIMITED  154243
3  L00000MH1946PLC197474     QUADRANT TELEVENTURES LIMITED  154244
4  L01100MH1996PLC100380                USHER AGRO LIMITED  154245

In [17]:
companyDf.index = companyDf.uuid

In [18]:
companyDf.head()

cin                              name    uuid
uuid                                                                   
154241  L00000CH1983PLC031318            SAB INDUSTRIES LIMITED  154241
154242  L00000CH1990PLC010573  LAKSHMI ENERGY AND FOODS LIMITED  154242
154243  L00000HP1994PLC014770        HITKARI INDUSTRIES LIMITED  154243
154244  L00000MH1946PLC197474     QUADRANT TELEVENTURES LIMITED  154244
154245  L01100MH1996PLC100380                USHER AGRO LIMITED  154245

In [19]:
uuidToNameDict = companyDf['name'].to_dict()

In [20]:
len(uuidToNameDict)

93492

In [25]:
c = 0
articles_covered = []
articles_count = 0
entities_resolved_with_graph = resolved_entities.find({'graphid':{'$exists':True}}, no_cursor_timeout=True)
for entity in entities_resolved_with_graph:
    articleIds = entity['articleIds']
    graphid = entity['graphid']
    type = entity['type']
    if not uuidToNameDict.get(graphid, None):
        continue
    print(entity['stdName'], entity['graphid'], uuidToNameDict[graphid])
    c += 1
    articles_covered += articleIds
    for aId in articleIds:
        doc = articlesColl.find_one({'_id':ObjectId(aId)})
        if not organizationArticles.find_one({'_id':ObjectId(aId)}):
            articles_count += 1
            organizationArticles.insert_one(doc)

ECL FINANCE LIMITED 129405 ECL FINANCE LIMITED
INVESTMENT CORPORATION (RATLAM) PRIVATE LIMITED 129050 INVESTMENT CORPORATION (RATLAM) PRIVATE LIMITED
ACE CREATIVE LEARNING PRIVATE LIMITED 150200 ACE CREATIVE LEARNING PRIVATE LIMITED
NATIONAL FILM DEVELOPMENT CORP0RATION LIMITED 152222 NATIONAL FILM DEVELOPMENT CORP0RATION LIMITED
SAMKRG PISTONS AND RINGS LIMITED 94242 SAMKRG PISTONS AND RINGS LIMITED
MUMBAI METRO TRANSPORT PRIVATE LIMITED 125713 MUMBAI METRO TRANSPORT PRIVATE LIMITED
NATIONAL INSTITUTE FOR SMART GOVERNMENT 151848 NATIONAL INSTITUTE FOR SMART GOVERNMENT
UDUPI POWER CORPORATION LIMITED 108421 UDUPI POWER CORPORATION LIMITED
PRATHAM EDUCATION FOUNDATION 150005 PRATHAM EDUCATION FOUNDATION
INVESTOR SERVICES OF INDIA LIMITED 139885 INVESTOR SERVICES OF INDIA LIMITED
AHMEDABAD STOCK EXCHANGE LIMITED 130983 AHMEDABAD STOCK EXCHANGE LIMITED
INDICUS FOUNDATION 140911 INDICUS FOUNDATION
GLOBAL EDUCATION LIMITED 236494 GLOBAL EDUCATION LIMITED
POABS ENTERPRISES PRIVATE LIMITED 96

VENTUREAST TRUST CAPITAL (INDIA) PRIVATE LIMITED 130673 VENTUREAST TRUST CAPITAL (INDIA) PRIVATE LIMITED
SREI MUTUAL FUND TRUST PRIVATE LIMITED 129473 SREI MUTUAL FUND TRUST PRIVATE LIMITED
GREEN GAS LIMITED 102568 GREEN GAS LIMITED
WENDT INDIA LIMITED 95879 WENDT INDIA LIMITED
KERALA STATE FINANCIAL ENTERPRISES LTD 128422 KERALA STATE FINANCIAL ENTERPRISES LTD
TRACTORS AND FARM EQUIPMENT LIMITED. 106814 TRACTORS AND FARM EQUIPMENT LIMITED.
HINDUSTAN PETROLEUM CORPORATION LIMITED 93686 HINDUSTAN PETROLEUM CORPORATION LIMITED
GOA STATE INFRASTRUCTURE DEVELOPMENT CORPORATION LIMITED 149935 GOA STATE INFRASTRUCTURE DEVELOPMENT CORPORATION LIMITED
VISHWA ORGANICS PVT LTD 213348 VISHWA ORGANICS PVT LTD
DHANLAXMI BANK LIMITED 95123 DHANLAXMI BANK LIMITED
PONDICHERRY TEXTILE CORPORATION LIMITED 100269 PONDICHERRY TEXTILE CORPORATION LIMITED
PERFECT RELATIONS PRIVATE LIMITED 145700 PERFECT RELATIONS PRIVATE LIMITED
KALYANPUR CEMENTS LTD 171178 KALYANPUR CEMENTS LTD
HINDUSTAN DORR OLIVER LIMITE

SHYAM TELECOM LIMITED 94523 SHYAM TELECOM LIMITED
AIA CSR FOUNDATION 237007 AIA CSR FOUNDATION
AJMERA REALTY & INFRA INDIA LIMITED 94155 AJMERA REALTY & INFRA INDIA LIMITED
KAIVALYA EDUCATION FOUNDATION 150051 KAIVALYA EDUCATION FOUNDATION
UMMEED CHILD DEVELOPMENT CENTRE 151845 UMMEED CHILD DEVELOPMENT CENTRE
NEOTERIC INFOMATIQUE LIMITED 107835 NEOTERIC INFOMATIQUE LIMITED
CHENNAI SUPER KINGS CRICKET LIMITED 147634 CHENNAI SUPER KINGS CRICKET LIMITED
INDIA POST PAYMENTS BANK LIMITED 235283 INDIA POST PAYMENTS BANK LIMITED
SHRIRAM PROPERTIES HOLDINGS PRIVATE LIMITED 114050 SHRIRAM PROPERTIES HOLDINGS PRIVATE LIMITED
KERALA TOURISM INFRASTRUCTURE LIMITED 124803 KERALA TOURISM INFRASTRUCTURE LIMITED
RAMKY PHARMA CITY (INDIA) LIMITED 104081 RAMKY PHARMA CITY (INDIA) LIMITED
KALLAM BROTHERS COTTONS PRIVATE LIMITED 100236 KALLAM BROTHERS COTTONS PRIVATE LIMITED
HINDUSTAN WIRES LTD 94174 HINDUSTAN WIRES LTD
BIHAR STATE TOURISM DEVELOPMENT CORPORATION LIMITED 224666 BIHAR STATE TOURISM DEVELOP

ESSAR MINERAL RESOURCES LIMITED 98427 ESSAR MINERAL RESOURCES LIMITED
SUNFLAG IRON AND STEEL CO LTD 94127 SUNFLAG IRON AND STEEL CO LTD
INDIAN RAILWAY CATERING AND TOURISM CORPORATION LIMITED 146304 INDIAN RAILWAY CATERING AND TOURISM CORPORATION LIMITED
SMARTCHEM TECHNOLOGIES LIMITED 227306 SMARTCHEM TECHNOLOGIES LIMITED
ASIAN PAINTS LIMITED 93842 ASIAN PAINTS LIMITED
APOLLO REACH HOSPITALS ENTERPRISES LIMITED 151472 APOLLO REACH HOSPITALS ENTERPRISES LIMITED
HATHWAY NASHIK CABLE NETWORK PRIVATE LIMITED 127043 HATHWAY NASHIK CABLE NETWORK PRIVATE LIMITED
MERCER CONSULTING (INDIA) PRIVATE LIMITED 119554 MERCER CONSULTING (INDIA) PRIVATE LIMITED
BINNY MILLS LIMITED 93512 BINNY MILLS LIMITED
MADRAS FERTILIZERS LIMITED 94517 MADRAS FERTILIZERS LIMITED
APARAJITHA CORPORATE SERVICES PRIVATE LIMITED 234924 APARAJITHA CORPORATE SERVICES PRIVATE LIMITED
KERALA STATE WOMEN'S DEVELOPMENT CORPORATION LIMITED 152120 KERALA STATE WOMEN'S DEVELOPMENT CORPORATION LIMITED
SMS PHARMACEUTICALS LIMITED 9

EXPRESS MEALS PRIVATE LIMITED 125358 EXPRESS MEALS PRIVATE LIMITED
AREVA T&D SYSTEMS INDIA LIMITED 111442 AREVA T&D SYSTEMS INDIA LIMITED
BHAGYANAGAR GAS LIMITED 111998 BHAGYANAGAR GAS LIMITED
WEST BENGAL GREEN ENERGY DEVELOPMENT CORPORATION LIMITED 111682 WEST BENGAL GREEN ENERGY DEVELOPMENT CORPORATION LIMITED
BYRAMJEE JEEJEEBHOY PRIVATE LIMITED 131399 BYRAMJEE JEEJEEBHOY PRIVATE LIMITED
BALASORE ALLOYS LIMITED 94140 BALASORE ALLOYS LIMITED
KILBURN ENGINEERING LIMITED 93908 KILBURN ENGINEERING LIMITED
SNS TEXTILES LIMITED 93472 SNS TEXTILES LIMITED
PEERLESS TRUST MANAGEMENT CO LIMITED 129471 PEERLESS TRUST MANAGEMENT CO LIMITED
ISOLUX CORSAN POWER CONCESSIONS INDIA PRIVATE LIMITED 111267 ISOLUX CORSAN POWER CONCESSIONS INDIA PRIVATE LIMITED
K.P.R. MILL LIMITED 93434 K.P.R. MILL LIMITED
U.P. PROJECTS CORPORATION LIMITED 99403 U.P. PROJECTS CORPORATION LIMITED
KOLKATA METRO RAIL CORPORATION LIMITED 125610 KOLKATA METRO RAIL CORPORATION LIMITED
WESTERN INDIA PLYWOODS LIMITED 93607 WESTE

...

PRAJO MULTISERVICES PRIVATE LIMITED 132885 PRAJO MULTISERVICES PRIVATE LIMITED
SOLITON TECHNOLOGIES PRIVATE LIMITED 98029 SOLITON TECHNOLOGIES PRIVATE LIMITED
OSL BALAJI ENTREPOT PRIVATE LIMITED 126872 OSL BALAJI ENTREPOT PRIVATE LIMITED
SUHASIT STAR TRADING PRIVATE LIMITED 223525 SUHASIT STAR TRADING PRIVATE LIMITED
FASEEMA TECHNOLOGIES PRIVATE LIMITED 102989 FASEEMA TECHNOLOGIES PRIVATE LIMITED
MUKESH HOLDINGS PRIVATE LIMITED 129004 MUKESH HOLDINGS PRIVATE LIMITED
BHORUKA MINES PRIVATE LIMITED 98587 BHORUKA MINES PRIVATE LIMITED
SOUTH CITY RECREATION PRIVATE LIMITED 218997 SOUTH CITY RECREATION PRIVATE LIMITED
SUBHKAM PROPERTIES PRIVATE LIMITED 116030 SUBHKAM PROPERTIES PRIVATE LIMITED
S C SHETH AND COMPANY PRIVATE LIMITED 121181 S C SHETH AND COMPANY PRIVATE LIMITED
CONCAST SHEETS AND TUBES LIMITED 106222 CONCAST SHEETS AND TUBES LIMITED
DENSO KIRLOSKAR INDUSTRIES PRIVATE LIMITED 109318 DENSO KIRLOSKAR INDUSTRIES PRIVATE LIMITED
PURANMAL PACKAGING AND MARKETING PRIVATE LIMITED 12353

AMRN NUTS PRIVATE LIMITED 235845 AMRN NUTS PRIVATE LIMITED
TANTRASOFT SOLUTIONS (INDIA) PRIVATE LIMITED 231490 TANTRASOFT SOLUTIONS (INDIA) PRIVATE LIMITED
SICPA INDIA PRIVATE LIMITED 101867 SICPA INDIA PRIVATE LIMITED
EDESK SERVICES LIMITED 211118 EDESK SERVICES LIMITED
AVASARALA TECHNOLOGIES LIMITED 151060 AVASARALA TECHNOLOGIES LIMITED
POLYMED HEALTHCARE (INDIA) PRIVATE LIMITED 103544 POLYMED HEALTHCARE (INDIA) PRIVATE LIMITED
CHL LIMITED 95021 CHL LIMITED
M2M CHIP PRIVATE LIMITED 102037 M2M CHIP PRIVATE LIMITED
RTC FOODWORKS LIMITED 125470 RTC FOODWORKS LIMITED
RACHIT FINSEC PRIVATE LIMITED 127433 RACHIT FINSEC PRIVATE LIMITED
ILANDFS AIRPORTS LIMITED 116621 ILANDFS AIRPORTS LIMITED
RAASI SOFTWARE CORPORATION LIMITED 139145 RAASI SOFTWARE CORPORATION LIMITED
SSPDL NORTHWOOD HOMES PRIVATE LIMITED 117103 SSPDL NORTHWOOD HOMES PRIVATE LIMITED
SICAL MINING LIMITED 210254 SICAL MINING LIMITED
ALFA DISTILLERIES PRIVATE LIMITED 99860 ALFA DISTILLERIES PRIVATE LIMITED
SEQUENT PHARMACEUTICA

QUASAR INDUSTRIES PRIVATE LIMITED 108109 QUASAR INDUSTRIES PRIVATE LIMITED
EMARS INFRASTRUCTURE PRIVATE LIMITED 118928 EMARS INFRASTRUCTURE PRIVATE LIMITED
ANSUYA MODY ENTERPRISES PRIVATE LIMITED 120568 ANSUYA MODY ENTERPRISES PRIVATE LIMITED
DOLPHIN HOLDINGS & REAL ESTATE PVT LTD 134051 DOLPHIN HOLDINGS & REAL ESTATE PVT LTD
PLG CLEAN ENERGY PROJECTS PRIVATE LIMITED 232086 PLG CLEAN ENERGY PROJECTS PRIVATE LIMITED
T&H EDUCATION PRIVATE LIMITED 150509 T&H EDUCATION PRIVATE LIMITED
ADMIRE COMMOSALE PRIVATE LIMITED 234816 ADMIRE COMMOSALE PRIVATE LIMITED
GROSVENOR ESTATES PRIVATE LIMITED 114201 GROSVENOR ESTATES PRIVATE LIMITED
M - TECH TOWNSHIP AND PROJECTS PRIVATE LIMITED 228881 M - TECH TOWNSHIP AND PROJECTS PRIVATE LIMITED
RAJASTHAN TUBE MANUFACTURING COMPANY LTD 169604 RAJASTHAN TUBE MANUFACTURING COMPANY LTD
R.P.INFO SYSTEMS LIMITED 231033 R.P.INFO SYSTEMS LIMITED
PIONEER COMMODITY INTERMEDIARIES PRIVATE LIMITED 222254 PIONEER COMMODITY INTERMEDIARIES PRIVATE LIMITED
HAUSSMAN IMPEX

MPACT TECHNOLOGY SERVICES PRIVATE LIMITED 138623 MPACT TECHNOLOGY SERVICES PRIVATE LIMITED
SUMEDHA INFRATECH PRIVATE LIMITED 117913 SUMEDHA INFRATECH PRIVATE LIMITED
PURE PERSONAL CARE LIMITED 223584 PURE PERSONAL CARE LIMITED
SUBHASH SILK MILLS LIMITED 171293 SUBHASH SILK MILLS LIMITED
SHIVA CONSULTANTS PRIVATE LIMITED 144772 SHIVA CONSULTANTS PRIVATE LIMITED
LAGOON CLUB PRIVATE LIMITED 144359 LAGOON CLUB PRIVATE LIMITED
PEL ASSET AND INFRASTRUCTURE LIMITED 114726 PEL ASSET AND INFRASTRUCTURE LIMITED
ARABINDA INFRASTRUCTURE PRIVATE LIMITED 135363 ARABINDA INFRASTRUCTURE PRIVATE LIMITED
DATAWORLD IT SERVICES LIMITED 231129 DATAWORLD IT SERVICES LIMITED
SUHAN AVIATION PRIVATE LIMITED 215950 SUHAN AVIATION PRIVATE LIMITED
IFCI LIMITED 95744 IFCI LIMITED
RAJASTHAN JAL VIKAS NIGAM LTD 149562 RAJASTHAN JAL VIKAS NIGAM LTD
ALOKIK AGRI FARMS PRIVATE LIMITED 97346 ALOKIK AGRI FARMS PRIVATE LIMITED
OASIS AGRITECH LIMITED 97039 OASIS AGRITECH LIMITED
NORTH EAST POWER AND INFRA LIMITED. 221974 NO

TGB BANQUETS AND HOTELS LIMITED 95017 TGB BANQUETS AND HOTELS LIMITED
VASWANI INDUSTRIES LIMITED 169764 VASWANI INDUSTRIES LIMITED
KOSAN INDUSTRIES PRIVATE LIMITED 102874 KOSAN INDUSTRIES PRIVATE LIMITED
BHANSALI NIPPON A&L PRIVATE LIMITED 237654 BHANSALI NIPPON A&L PRIVATE LIMITED
MULTIDIMENSION ENTERTAINMENTS PRIVATE LIMITED 234955 MULTIDIMENSION ENTERTAINMENTS PRIVATE LIMITED
LONGEVITY DEVELOPERS PRIVATE LIMITED 113466 LONGEVITY DEVELOPERS PRIVATE LIMITED
VANYATA ESTATES PRIVATE LIMITED 133415 VANYATA ESTATES PRIVATE LIMITED
CFM ASSET RECONSTRUCTION PRIVATE LIMITED 232476 CFM ASSET RECONSTRUCTION PRIVATE LIMITED
INTERFACE FINANCIAL SERVICES LTD 171849 INTERFACE FINANCIAL SERVICES LTD
BUDHRANI FINANCE LIMITED 127814 BUDHRANI FINANCE LIMITED
HUG FOODS PRIVATE LIMITED 124302 HUG FOODS PRIVATE LIMITED
MONARCH FARMS PRIVATE LIMITED 233370 MONARCH FARMS PRIVATE LIMITED
BINAWADINI PRINTING & ALLIED WORKS PRIVATE LIMITED 215171 BINAWADINI PRINTING & ALLIED WORKS PRIVATE LIMITED
GLOWVIEW PRO

In [26]:
print(c, articles_count, len(set(articles_covered)))
organizationArticles.find({}).count()

93364 34258 34258


34258